# Intro to language model

Part 1 - Intro to language modeling:
- Counting bigrams in 2D torch tensor ("training")
- From counts to probabilities (vectorization)
- Sampling from the model
- Loss function
- Smoothing

Part 2 - Simple MLP for Language Modeling:
- Understanding the model
- Simple training loop

Part 3 - Learning subword tokens

Sources: 
- https://github.com/karpathy/nn-zero-to-hero
- https://github.com/karpathy/makemore

Resources:
- https://huggingface.co/course/chapter1/1

In [ ]:
import torch
import torch.nn.functional as F
import matplotlib.pyplot as plt
from collections import defaultdict
%matplotlib inline

In [ ]:
# download the names.txt file from github
!wget -O names.txt https://raw.githubusercontent.com/karpathy/makemore/master/names.txt
# !wget https://raw.githubusercontent.com/karpathy/char-rnn/master/data/tinyshakespeare/input.txt

In [ ]:
words = open('names.txt', 'r').read().splitlines()

In [ ]:
words[:10]

In [ ]:
len(words)

In [ ]:
min(len(w) for w in words)

In [ ]:
max(len(w) for w in words)

Example Bigrams

In [ ]:
# Show the bigram examples

## Part 1 - Intro to language modeling

### Counting bigrams in 2D torch tensor ("training")

In [ ]:
vocab_dim = 27

In [ ]:
# https://pytorch.org/docs/stable/torch.html#creation-ops
# Rows: first character, columns: second character
N = torch.zeros((vocab_dim, vocab_dim), dtype=torch.int32)
# Check the the shape
N

Example Tensor/Indexing/Manipulation

In [ ]:
# Create a mapping from character to index and from index to character
chars = sorted(list(set(''.join(words))))
# stoi = {s:i+1 for i,s in enumerate(chars)}
# stoi['.'] = 0
# itos = {i:s for s,i in stoi.items()}

In [ ]:
for w in words:
  chs = ['.'] + list(w) + ['.']
  for ch1, ch2 in zip(chs, chs[1:]):
    ix1 = stoi[ch1]
    ix2 = stoi[ch2]
    N[ix1, ix2] += 1

In [ ]:
plt.figure(figsize=(16,16))
plt.imshow(N, cmap='Blues')
for i in range(vocab_dim):
    for j in range(vocab_dim):
        chstr = itos[i] + itos[j]
        plt.text(j, i, chstr, ha="center", va="bottom", color='gray')
        plt.text(j, i, N[i, j].item(), ha="center", va="top", color='gray')
plt.axis('off');

### From counts to probabilities

In [ ]:
N[0,:]


Simple normalizing

In [ ]:
# Simple normalizing
p = N[-1].float()
# Divides each element of p by the sum of p
p = p / p.sum()
p

Normalizing with broadcasting

In [ ]:
# Broadcasting
# https://pytorch.org/docs/stable/notes/broadcasting.html
P = N.float()
# Dim and keep dim
row_sum = P.sum(dim=1, keepdim=True)
print(row_sum.shape)
# Normalize (Copy the column sums across columns)
P /= row_sum

In [ ]:
# 27, 27
# 27, 1

In [ ]:
P.sum(1)

In [ ]:
# Pitfalls of broadcasting
P = N.float()
# dim=1, keep_dim=False
row_sum = P.sum(dim=1)
P /= row_sum
print(row_sum.shape)

In [ ]:
P.sum(1)

In [ ]:
# 27, 27
#  1  27
# ==> Copys sum across columns over the rows

### Sampling

Starting from the "." token

In [ ]:
g = torch.Generator().manual_seed(42)
# What is ix telling us
ix = torch.multinomial(P[0], num_samples=1, replacement=True, generator=g).item()
# What is itos[ix]?
# itos[ix]

Generating names

In [ ]:
g = torch.Generator().manual_seed(42)

for i in range(1):
  out = []
  ix = 0
  while True:
    p = P[ix]
    ix = torch.multinomial(p, num_samples=1, replacement=True, generator=g).item()
    out.append(itos[ix])
    if ix == 0:
      break
  print(''.join(out[:-1]))

In [ ]:
Compare against the uniform model

### Loss function
https://en.wikipedia.org/wiki/Maximum_likelihood_estimation

In [ ]:
# GOAL: maximize likelihood of the data w.r.t. model parameters (statistical modeling) ==> Slide 9, Lecture 2
# equivalent to maximizing the log likelihood (because log is monotonic)
# equivalent to minimizing the negative log likelihood
# equivalent to minimizing the average negative log likelihood

# log(a*b*c) = log(a) + log(b) + log(c)

In [ ]:
log_likelihood = 0.0
n = 0

for w in words:
# for w in ["wilhelm"]: # "wilhelmq"
  chs = ['.'] + list(w) + ['.']
  for ch1, ch2 in zip(chs, chs[1:]):
    ix1 = stoi[ch1]
    ix2 = stoi[ch2]
    prob = P[ix1, ix2]
    logprob = torch.log(prob)
    log_likelihood += logprob
    n += 1
    # print(f'{ch1}{ch2}: {prob:.4f} {logprob:.4f}')

print(f'{log_likelihood=}')
nll = -log_likelihood
print(f'{nll=}')
print(f'{nll/n}')

### Additive Smoothing
https://en.wikipedia.org/wiki/Additive_smoothing

In [ ]:
P = (N+1).float()
P /= P.sum(1, keepdims=True)

## Part 2 - Simple MLP for Language Modeling
https://www.jmlr.org/papers/volume3/bengio03a/bengio03a.pdf

### Understanding the model

In [ ]:
# Build the training data

block_size = 3 # context length: how many characters do we take to predict the next one?
X, Y = [], []
for w in words[:5]:
  
  print(w)
  context = [0] * block_size
  for ch in w + '.':
    ix = stoi[ch]
    X.append(context)
    Y.append(ix)
    print(''.join(itos[i] for i in context), '--->', itos[ix])
    context = context[1:] + [ix] # crop and append
  
X = torch.tensor(X)
Y = torch.tensor(Y)

In [ ]:
X.shape, X.dtype, Y.shape, Y.dtype

In [ ]:
# build the dataset
block_size = 3 # context length: how many characters do we take to predict the next one?

def build_dataset(words):  
  X, Y = [], []
  for w in words:

    #print(w)
    context = [0] * block_size
    for ch in w + '.':
      ix = stoi[ch]
      X.append(context)
      Y.append(ix)
      #print(''.join(itos[i] for i in context), '--->', itos[ix])
      context = context[1:] + [ix] # crop and append

  X = torch.tensor(X)
  Y = torch.tensor(Y)
  print(X.shape, Y.shape)
  return X, Y

import random
random.seed(42)
random.shuffle(words)
n1 = int(0.8*len(words))
n2 = int(0.9*len(words))


### Why do we split into train, dev and test ###
Xtr, Ytr = build_dataset(words[:n1])
Xdev, Ydev = build_dataset(words[n1:n2])
Xte, Yte = build_dataset(words[n2:])

In [ ]:
# Embedding Matrix
C = torch.randn((27, 2))

In [ ]:
# Dummy training examples
X.shape

In [ ]:
X[0]
# print("".join([itos[x.item()] for x in X[0]]))

In [ ]:
# one = F.one_hot(X[0], num_classes=27).float()
# one @ C
# h = (one @ C).mean(0)

In [ ]:
# Indexing
C[X[0]]
# C[[0,0,0]]
# C[[0,0,0]].shape

In [ ]:
# Index our training examples from our embedding matrix
emb = C[X]
emb.shape

In [ ]:
# Reshaping tensors
# emb[0].view(1,6)
# emb[0].view(-1,6)

In [ ]:
# First linear layer | What is the dimension?
W1 = torch.randn((6, 100))
b1 = torch.randn(100)

In [ ]:
# Dense intermediate representation of our input
h = torch.tanh(emb.view(-1, 6) @ W1 + b1)

In [ ]:
h

In [ ]:
h.shape

In [ ]:
# Up-projection | What is the dimension?
W2 = torch.randn((100, 27))
b2 = torch.randn(27)

In [ ]:
logits = h @ W2 + b2

In [ ]:
logits.shape

In [ ]:
counts = logits.exp()

In [ ]:
prob = counts / counts.sum(1, keepdims=True)

In [ ]:
prob.shape

In [ ]:
F.softmax(logits, dim=1).allclose(prob)

In [ ]:
Y[:5]

In [ ]:
torch.arange(32)

In [ ]:
loss = -prob[torch.arange(32), Y].log().mean()
loss.item()

In [ ]:
F.cross_entropy(logits, Y).allclose(loss)

### Simple training loop

In [ ]:
#---putting it together---
vocab_size = len(itos)
emb_dim = 2
block_size = 3
h_dim = 100
g = torch.Generator().manual_seed(42) # for reproducibility
C = torch.randn((vocab_size, emb_dim), generator=g)
W1 = torch.randn((emb_dim * block_size, h_dim), generator=g)
b1 = torch.randn(h_dim, generator=g)
W2 = torch.randn((h_dim, vocab_size), generator=g)
b2 = torch.randn(vocab_size , generator=g)
parameters = [C, W1, b1, W2, b2]

In [ ]:
sum(p.nelement() for p in parameters) # number of parameters in total

In [ ]:
for p in parameters:
    print(p.requires_grad)

In [ ]:
for p in parameters:
  p.requires_grad = True

In [ ]:
lr=0.1
max_steps = 100000
losses = []
batch_size = 32

for i in range(max_steps):
    # Batching
    ix = torch.randint(low=0, high=Xtr.shape[0], size=(batch_size,)) # What do we get here?
    
    # Forward pass
    emb = C[Xtr[ix]] # (batch_size, block_size, emb_dim) => (32, 3, 2)
    h = torch.tanh(emb.view(-1, block_size*emb_dim) @ W1 + b1) # (32, 100)
    logits = h @ W2 + b2 # (32, 27)
    loss = F.cross_entropy(logits, Ytr[ix])
    
    # Reset gradients
    for p in parameters:
        p.grad = None
        
    # Backward pass
    loss.backward()
    
    # Stochastic gradient descent
    for p in parameters:
        p.data += -lr * p.grad

    # track stats
    if i % 10000 == 0: # print every once in a while
        print(f'{i:7d}/{max_steps:7d}: {loss.item():.4f}')
    losses.append(loss.item())

In [ ]:
plt.plot(torch.tensor(losses).view(-1, 1000).mean(1))

In [ ]:
@torch.no_grad() # this decorator disables gradient tracking inside pytorch
def split_loss(split):
    x,y = {
        'train': (Xtr, Ytr),
        'val': (Xdev, Ydev),
    }[split]
    emb = C[x]
    h = torch.tanh(emb.view(-1, block_size*emb_dim) @ W1 + b1)
    logits = h @ W2 + b2
    loss = F.cross_entropy(logits, y)
    print(split, loss.item())

split_loss('train')
split_loss('val')

In [ ]:
# visualize dimensions 0 and 1 of the embedding matrix C for all characters
plt.figure(figsize=(8,8))
plt.scatter(C[:,0].data, C[:,1].data, s=200)
for i in range(C.shape[0]):
    plt.text(C[i,0].item(), C[i,1].item(), itos[i], ha="center", va="center", color='white')
plt.grid('minor')

In [ ]:
# sample from the model
g = torch.Generator().manual_seed(42)

for _ in range(20):
    
    out = []
    context = [0] * block_size # initialize with all ...
    while True:
      emb = C[torch.tensor([context])] # (1,block_size,d)
      h = torch.tanh(emb.view(1, -1) @ W1 + b1)
      logits = h @ W2 + b2
      probs = F.softmax(logits, dim=1)
      ix = torch.multinomial(probs, num_samples=1, generator=g).item()
      context = context[1:] + [ix]
      out.append(ix)
      if ix == 0:
        break
    
    print(''.join(itos[i] for i in out[:-1]))

In [ ]:
How to get to CBOW
- One hot indexing
- Averaging of embeddings
- Simple up-projection

## Part 3: Learning subword tokens (WordPiece)
https://arxiv.org/pdf/1609.08144.pdf

In [ ]:
# 1. Example single word "word"
corpus = "word"
vocab = ['w', '##o', '##r', '##d']
split_corpus = [('w', '##o', '##r', '##d', 1)]

In [ ]:
# f(t1,t2)/(f(t1)*f(t2))
# Intuition: Dampen the effect of generally frequent tokens

In [ ]:
# 2. Example 
("hug", 10), ("pug", 5), ("pun", 12), ("bun", 4), ("hugs", 5)
vocab = ["b", "h", "p", "##g", "##n", "##s", "##u"]
split_corpus = ("h" "##u" "##g", 10), ("p" "##u" "##g", 5), ("p" "##u" "##n", 12), ("b" "##u" "##n", 4), ("h" "##u" "##g" "##s", 5)
# First merge ==> ##g,##s ==> ##gs
vocab = ["b", "h", "p", "##g", "##n", "##s", "##u", "##gs"]
split_corpus = ("h" "##u" "##g", 10), ("p" "##u" "##g", 5), ("p" "##u" "##n", 12), ("b" "##u" "##n", 4), ("h" "##u" "##gs", 5)
# Second merge ==> h, ##u
vocab = ["b", "h", "p", "##g", "##n", "##s", "##u", "##gs", "hu"]
split_corpus = ("hu" "##g", 10), ("p" "##u" "##g", 5), ("p" "##u" "##n", 12), ("b" "##u" "##n", 4), ("hu" "##gs", 5)
# Third merge ==> hu, ##g
vocab = ["b", "h", "p", "##g", "##n", "##s", "##u", "##gs", "hu", "hug"]
split_corpus = ("hug", 10), ("p" "##u" "##g", 5), ("p" "##u" "##n", 12), ("b" "##u" "##n", 4), ("hu" "##gs", 5)
# Continue until desired vocab size is reached

In [ ]:
# Tokenization of token "hugs"
# 1. Find longest subword starting from the beginning in the vocabulary ==> "hug"
# 2. Split the token:
split = ["hug", "##s"]
# 1. Find longest subword starting from the beginning in the vocabulary ==> "##s"
tokenization = ["hug", "##s"]

In [ ]:
# Tokenization of the token "mug"
# 1. Find longest subword starting from the beginning in the vocabulary ==> "[UNK]" ("m" is not in the vocabulary)
tokenization = ["[UNK]"]

In [ ]:
# Tokenization of the word "bum"
# 1. Find longest subword starting from the beginning in the vocabulary ==> "b"
# 2. Split the token:
split = ["b", "##um"]
# 1. Find longest subword starting from the beginning in the vocabulary ==> "##u"
# 2. Split the token:
split = ["b", "##u", '##m']
# 1. Find longest subword starting from the beginning in the vocabulary ==> "[UNK]"
tokenization = ["[UNK]"]

In [ ]:
# Apply text preprocessing (normalization, pre-tokenization) if working text 

# Getting the word frequencies
word_freqs = defaultdict(int)
for word in words:
    word_freqs[word] += 1

print(list(word_freqs.items()))
# word_freqs

In [ ]:
# Getting the alphabet (pre-vocab)
alphabet = []
for word in word_freqs.keys():
    if word[0] not in alphabet:
        alphabet.append(word[0])
    for letter in word[1:]:
        if f"##{letter}" not in alphabet:
            alphabet.append(f"##{letter}")

alphabet.sort()
print(alphabet)
        

In [ ]:
# In case of pretrained language models more special tokens are used ("[UNK]", "[CLS]", ...)
vocab = ["."] + alphabet.copy() 
print(vocab)

In [ ]:
# Create our splitted corpus: {"emma": [e, ##m, ##m, ##a]}
splits = {
    word: [c if i == 0 else f"##{c}" for i, c in enumerate(word)]
    for word in word_freqs.keys()
}
print(list(splits.items())[:5])

In [ ]:
# "Training" aka learn the merges
# Compute the score for each pair that can be constructed from splits
def compute_pair_scores(splits):
    letter_freqs = defaultdict(int)
    pair_freqs = defaultdict(int)
    for word, freq in word_freqs.items(): 
        split = splits[word] 
        if len(split) == 1:
            # Word is a single token
            letter_freqs[split[0]] += freq
            continue
        for i in range(len(split) - 1):
            # Construct pairs from left to right
            pair = (split[i], split[i + 1])
            # Update the frequency of the current "letter"/subword
            letter_freqs[split[i]] += freq
            # Update the frequency of the pair
            pair_freqs[pair] += freq
        # Update the frequency of the last "letter"/subword
        letter_freqs[split[-1]] += freq

    scores = {
        pair: freq / (letter_freqs[pair[0]] * letter_freqs[pair[1]])
        for pair, freq in pair_freqs.items()
    }
    return scores

In [ ]:
# Let´s look at the first scores
pair_scores = compute_pair_scores(splits)
for i, key in enumerate(pair_scores.keys()):
    print(f"{key}: {pair_scores[key]}")
    if i >= 5:
        break

In [ ]:
# Get the best pair
max(pair_scores.items(), key=lambda kv: kv[1])

In [ ]:
# Append to vocab
vocab.append("qu")

In [ ]:
# Apply the update vocabulary to splits
def merge_pair(a, b, splits):
    for word in word_freqs: # yuheng
        split = splits[word] # ['y', '##u', '##h', '##e', '##n', '##g']
        if len(split) == 1:
            continue
        i = 0
        while i < len(split) - 1:
            if split[i] == a and split[i + 1] == b:
                merge = a + b[2:] if b.startswith("##") else a + b
                split = split[:i] + [merge] + split[i + 2 :]
            else:
                i += 1
        splits[word] = split
    return splits

In [ ]:
splits = merge_pair("q", "##u", splits)
splits["quinn"]

In [ ]:
# Let´s build our vocabulary
vocab_size = 200
while len(vocab) < vocab_size:
    # Compute pair scores
    scores = compute_pair_scores(splits)
    # Get best pair
    best_pair, max_score = max(scores.items(), key=lambda kv: kv[1])
    # Update splits / corpus (merge)
    splits = merge_pair(*best_pair, splits)
    # Add new token to vocab
    new_token = (
        best_pair[0] + best_pair[1][2:]
        if best_pair[1].startswith("##")
        else best_pair[0] + best_pair[1]
    )
    vocab.append(new_token)

In [ ]:
print(vocab)

In [ ]:
# Encode a word, search for the longest substring
def encode_word(word): # emma
    tokens = []
    while len(word) > 0:
        i = len(word) # i = 4
        while i > 0 and word[:i] not in vocab:
            i -= 1
        tokens.append(word[:i])
        word = word[i:]
        if len(word) > 0:
            word = f"##{word}"
    return tokens

In [ ]:
print(encode_word("emma"))
print(encode_word("quinn"))

### Coding Exercises:
- "Train" a subword level bigram or a character level trigram model
- "Train" a character level bigram model on tiny shakespeare
- Train a character level bigram model with stochastic gradient descent (no counting, but learn the probabilities via gradient descent and backprop)
- Train a simple MLP on tiny shakespeare
- Add the residual connection to the simple MLP

### 

### Pen & Paper Exercises:

- Build the subword vocabulary with a vocabulary size of 10 for the following sentence: "hug pup hug pup pun hugs hug pup un" using WordPiece. Don´t add the "." token to your alphabet.
    - Solution: ['##g', '##n', '##p', '##s', '##u', 'h', 'p', 'u', 'un', '##gs']
- Tokenize the word "hug" with your learned vocabulary using WordPiece.
    - Solution: ['h', '##u', '##g']
- Compute the character-level bigram probabilities for the following corpus using additive smoothing (+ 1): ["baba", "abba", "abba", "abab", "bbba"]. Build all possible bigrams: ["..", ".a", ".b", "a.", "b.", "aa", "ab", "ba", "bb"].
    - Solution:
        - ..: 0.125
        - .a: 0.500
        - .b: 0.3750
        - a.: 0.4167
        - b.: 0.1429
        - aa: 0.0833
        - ab: 0.5000
        - ba: 0.5000
        - bb: 0.3571
- Compute the unnormalized negative log-likelihood of the word "bab" in your character-level bigram model:
    - Solution: 4.3130
- Compute the logits for a CBOW model
    - Sentence: "Frodo and Sam fight the orks"
    - Vocab: ["Frodo", "Sam", "fight", "the", "orks"]
    - Compute the logits for a CBOW model for the word "fight" being the center word with a window size of 2 given the matrics W1 and W2 (below)
    - Solution: [ 0.6394, -0.7976, -0.1091,  1.5486, -0.9377]
- What are the differences between BPE and WordPiece and SentencePiece?

In [ ]:
W1 = 
[[ 0.4128, -0.2592, -0.5713, -0.9116],
 [-0.6286,  0.1850,  0.8611,  0.3844],
 [ 2.0777,  0.2960, -0.7118,  1.0722],
 [-1.0484,  0.9931,  0.2309,  2.5170],
 [ 1.8805,  1.0564,  1.7468,  0.2562]]

In [ ]:
W2 =
[[-0.9120, -0.7972, -0.1510, -0.0237, -0.1716],
 [-0.0279, -0.2131, -1.2196, -0.1247,  0.0168],
 [ 0.9730, -1.0510, -0.6692,  1.5317, -1.4178],
 [ 0.4312,  0.0468,  1.5954,  1.3278, -0.2063]]